In [1]:
%matplotlib inline

# Assignment 3

**DUE: Tuesday, February 14th 2022 at 11:59pm**

Turn in the assignment via Canvas.

To write legible answers you will need to be familiar with both [Markdown](https://github.com/adam-p/markdown-here/wiki/Markdown-Cheatsheet) and [Latex](https://www.latex-tutorial.com/tutorials/amsmath/)

Before you turn this problem in, make sure everything runs as expected. To do so, restart the kernel and run all cells (in the menubar, select Runtime→→Restart and run all).
#### Show your work!
Whenever you are asked to find the solution to a problem, be sure to also **show how you arrived** at your answer.

### Resources

[1] https://community.plotly.com/t/two-3d-surface-with-different-color-map/18931/2 (Different color plots plotly)

[2] https://plotly.com/python/3d-surface-plots/ [plotting surfaces]

[3] https://community.plotly.com/t/3d-scatter-plot-with-surface-plot/27556/5 [plotting scatter plots]

[4] https://community.plotly.com/t/what-colorscales-are-available-in-plotly-and-which-are-the-default/2079 [color scales]

In [2]:
%matplotlib inline

In [3]:
NAME = "Jeshwanth Bheemanpally"
STUDENT_ID = "1588863"

## Problem 1: Local Search on the Ackley Surface
---

As discussed in class with Local Search problems the path to the goal is not as important as the goal itself. In this question we work with the Ackley function, a non-convex function typically used as a test for optimization algorithms.

The Achkey function has many local optima but only one global optimum that is $f(0,0) = 0$. Interestingly enough it might not be that easy to find this solution.

The Ackley function is defined as:

$$f(x,y):= -20exp[-0.2\sqrt{0.5(x^2 + y^2)}] -exp[0.5(cos(2\pi x) + cos(2\pi y))] + e + 20$$

The figure below illustrates the result of running three optimization methods on the Ackley Function. These solutions were found using methods A, B and C.


![](https://drive.google.com/uc?id=1K0_iokZu-TgjD0xrfGmWQbb-r67kINI0)



In this question, you will implement 3 optimization algorithms: 

1.   Stochastic Hill Climbing with Restarts (SHCR)
2.   Simulated Annealing (SA)
3.   Local Beam Search (LBS)

**Deliverables**

1. Complete this Notebook with implementation of SHCR, SA and LBS.
2. For each algorithm **visualize** the candidate solutions found at each
step using the provided ```create_ackley_figure()``` function. please see the image above an example of an image that should be included in your submission.



In [4]:
import numpy as np
from numpy import arange
from numpy import exp
from numpy import sqrt
from numpy import cos
from numpy import e
from numpy import pi
from numpy import meshgrid
from numpy.random import randn
from numpy.random import rand
from numpy.random import seed
from numpy.random import uniform
# hill climbing search of the ackley objective function
from numpy import asarray
import plotly.graph_objects as go

# objective function
def f(x, y):
	return -20.0 * exp(-0.2 * sqrt(0.5 * (x**2 + y**2))) - exp(0.5 * (cos(2 * pi * x) + cos(2 * pi * y))) + e + 20

def create_ackley_figure(solution_points=np.array([]), soln_names=['A','B,','C']):
  """
  :param solution_points A numpy array of dimensions [i, n, 2]
  where i is the number of solution points you want to plot and n is the 
  number of steps used in estimating your solution. In each case use the same 
  number of steps if you want to plot all solutions on the same figure.

  :return An interactive Ackley function figure with/without solution points.
  """
  # define range for input
  r_min, r_max = -5.0, 5.0
  # sample input range uniformly at 0.1 increments
  xaxis = arange(r_min, r_max, 0.1) # (100,)
  yaxis = arange(r_min, r_max, 0.1) # (100,)
  # create a mesh from the axis
  x, y = meshgrid(xaxis, yaxis)

  # compute targets
  results = f(x, y)

  figure = go.Figure(data=[go.Surface(z=results, x=x, y=y,colorscale='Blues',showscale=False)])
  figure.update_layout(title='Ackley Function', autosize=False,
                  width=500, height=500,
                  margin=dict(l=65, r=50, b=65, t=90))
  
  if solution_points.size:
    soln_colors = ['Reds', 'Rainbow', 'Viridis']
    for i in range(len(solution_points)):
      x_sln = solution_points[i][:,0]
      y_sln = solution_points[i][:,1]
      zdata = f(x_sln, y_sln)
      figure.add_scatter3d(name=soln_names[i], x=x_sln, y=y_sln, z=zdata, mode='markers',
      marker=dict(size=1, color=x_sln.flatten(), colorscale=soln_colors[i]))
      
      figure.update_layout(showlegend=True)
      
  return figure

In [5]:
### RUN THIS ###
"""
This is the Ackley Function.
"""
ack_figure = create_ackley_figure()
ack_figure

### General Function Definitions

In [6]:
# objective function
def objective(v):
  """
  This function defines the Ackley surface, it has a minimum of 0. This 
  can be used to test if we have found points that yield the minimum value.
  :param v, a tuple representing a 2D point being tested.

  returns a value in the range [-5.0, 5.0]
  """
  x, y = v
  return -20.0 * exp(-0.2 * sqrt(0.5 * (x**2 + y**2))) - exp(0.5 * (cos(2 * pi * x) + cos(2 * pi * y))) + e + 20

  
# check if a point is within the bounds of the search
def in_bounds(point, bounds=asarray([[-5.0, 5.0], [-5.0, 5.0]])):
  """
  It is possible our optimzation method could move us outside of our search 
  space, so it is helpful to check.
  :param point a tuple representing a 2D point
  :param a 2D array, that describes the bounds of each dimension of our point.
  returns a Boolean of whether the point lies in the bounds or not.
  """
	# enumerate all dimensions of the point
  for d in range(len(bounds)):
    # check if out of bounds for this dimension
    if point[d] < bounds[d, 0] or point[d] > bounds[d, 1]:
      return False
  return True

### Part 1) Stochastic Hill Climbing with Restarts

1.   Implement SHCR in the cell below.
2.   Visualize and comment on the candidate points visited.


In [7]:
from numpy import random
# stochastic hill climbing with restarts algorithm
def stochastic_hillclimbing(objective, bounds, n_iterations, step_size, start_pt):
  """
  :param objective, the function we are trying to optimize
  :param bounds, the boundaries of the problem
  :param n_iterations number of times to repeat stochastic hill climbing
  :param step_size how much we should move
  :param start_pt the point we start optimizing from.
  returns [solution, solution_value, candidates]
  """
  ### YOUR CODE HERE ###
  current_point = start_pt
  candidates = []

  for iteration in range(0, n_iterations):
      # random neighbor of up to step_size
    
      neighbor = current_point + random.uniform(low = -1, high = 1, size = len(bounds)) * step_size
      while not(in_bounds(neighbor)):
            neighbor = current_point + random.uniform(low = -1, high = 1, size = len(bounds)) * step_size
      
      candidates.append(neighbor)
      score = objective(neighbor)
      # trying to find mini max 
      if score <= objective(current_point):
        current_point = neighbor

  return [current_point, objective(current_point), candidates]

def random_restarts(objective, bounds, n_iter, step_size, n_restarts):
  """
  :param objective, the function we are trying to optimize
  :param bounds, the boundaries of the problem
  :param n_iter number of times to repeat stochastic hill climbing 
  :param step_size how much we should move
  :param n_restarts, the number of times we restart.
  returns [best solution, best solution value, visited points]
  """
  ### YOUR CODE HERE ###
  iteration_solution = []
  for iteration in range(0, n_restarts):
      start_position = rand(2)
      start_position[0] = start_position[0] * (bounds[0][-1] - bounds[0][0]) + bounds[0][0]
      start_position[1] = start_position[1] * (bounds[1][-1] - bounds[1][0]) + bounds[1][0]
      result = stochastic_hillclimbing(objective, bounds, n_iter, step_size, start_position)
      iteration_solution.append(result)

  best_solution = min(iteration_solution, key = lambda k: k[1])
  best_solution[-1] = np.array([data[-1] for data in iteration_solution]).reshape(-1, 2)

  return min(iteration_solution, key = lambda k: k[1])

# seed the pseudorandom number generator
seed(240)
# define range for input
bounds = asarray([[-5.0, 5.0], [-5.0, 5.0]])
# define the total iterations
n_iter = 1000
# define the maximum step size
step_size = 0.05
# total number of random restarts
n_restarts = 30
# perform the hill climbing search
best, score, shcr_candidates = random_restarts(objective, bounds, n_iter, step_size, n_restarts)
print('Done!')
print('f(%s) = %f' % (best, score))

Done!
f([-0.00182561 -0.00062036]) = 0.005553


##### Analysis - Stochastic Hill Climbing


In [8]:
# Analysis
all_method_candidates = np.array([shcr_candidates])
ack_figure = create_ackley_figure(all_method_candidates)
ack_figure.show()


The figure depicts each search path for the given random restarts done for the stochastic hill algorithm. Eventually, after a certain number of restarts, we choose an initial point close enought to the optimum at f(0,0) so that SHC was able to find the point. This demonstrates how SHC with restarts is asymtotically complete, as it will evenutally reach the global minimum after a asymptotic number of random restarts.

### Part 2) Simulated Annealing

1.   Implement SA in the cell below.
2.   Visualize and comment on the candidate points visited.

In [9]:
def get_temperature_schedule(epoch, temp, diff):
  """
  :param temp Temperature
  :param epoch Iterations elapsed
  :param diff Difference between value of candidate solution and value of best solution so far.
  """
  # calculate temperature for current epoch
  t = temp / float(epoch + 1)
  # calculate acceptance criterion
  criterion = exp(-diff / t)
  return criterion

# simulated annealing algorithm
def simulated_annealing(objective, bounds, n_iterations, step_size, temp):
  """ 
  :param objective, the function we are trying to optimize
  :param bounds, the boundaries of the problem
  :param n_iterations number of times to repeat stochastic hill climbing
  :param step_size how much we should move
  :param temp temperature for each epoch
  returns [solution, solution_value, candidates] 
  """
  ### YOUR CODE HERE ###
  current_solution = rand(2)
  current_solution[0] = current_solution[0] * (bounds[0][-1] - bounds[0][0]) + bounds[0][0]
  current_solution[1] = current_solution[1] * (bounds[1][-1] - bounds[1][0]) + bounds[1][0]


  current_solution_value = objective(current_solution)
  candidates = []

  current_epoch = 0
  for iteration in range(0, n_iterations):
      
      neighbor = current_solution + (random.uniform(low = -1, high = 1, size = len(bounds)) * step_size)
      while not(in_bounds(neighbor)):
         neighbor = current_solution + (random.uniform(low = -1, high = 1, size = len(bounds)) * step_size)

      candidates.append(neighbor)
      delta_e = objective(neighbor) - objective(current_solution)
      weight = get_temperature_schedule(current_epoch, temp, delta_e)

      if weight == 0:
          break
    
      if delta_e < 0:
          current_solution = neighbor
          current_solution_value = objective(neighbor)
      elif random.choice(2, 1, p=[1.0 - weight, weight])[0] == 1:
          current_solution = neighbor
          current_solution_value = objective(neighbor)
      current_epoch += 1



  return current_solution, current_solution_value, candidates

# seed the pseudorandom number generator
seed(240)
# define range for input
bounds = asarray([[-5.0, 5.0], [-5.0, 5.0]])
# define the total iterations
n_iterations = 1000
# define the maximum step size
step_size = 0.5
# initial temperature
temp = 10
# perform the simulated annealing search
best, score, sa_candidates = simulated_annealing(objective, bounds, n_iterations, step_size, temp)
print('Done!')
print('f(%s) = %f' % (best, score))

Done!
f([-0.01093516  0.01515641]) = 0.062141


In [10]:
# Analysis
all_method_candidates = np.array([sa_candidates])
ack_figure = create_ackley_figure(all_method_candidates)
ack_figure.show()

### Analysis - Simulated Annealing

The original hyperparameters, where the step size is 0.1 caused the algorithm to be stuck at the local minimum. By increasing the step size to 0.5, the algorithm now reaches close to the global minimum. 

### Part 3) Local Beam Search



1.   Implement LBS in the cell below.
2.   Visualize and comment on the candidate points visited.
3.   Compare all 3 implementations by commenting on the distribution of points on the Ackley surface and the empirical run time of each method.


In [11]:
# generate the neighbors based on step size
def generate_neighbors(point, step_size=0.1):
    point = point.reshape(-1,1)
    possible_steps = possible_steps = np.array([[step_size*i for i in range(-10,11)],
                           [step_size*i for i in range(-10,11)]])
    neighbors = point + possible_steps
    return neighbors

def local_beam_search(objective, bounds, step_size, k, n_iterations):
  """ 
  :param objective, the function we are trying to optimize
  :param bounds, the boundaries of the problem
  :param k, how many candidates to consider
  :param n_iterations, how long to search for.
  returns [solution, solution_value, candidates] 
  """
  ### YOUR CODE HERE ###

  current_beam = []

  while len(current_beam) != k:
    point = rand(2)
    point[0] = point[0] * (bounds[0][-1] - bounds[0][0]) + bounds[0][0]
    point[1] = point[1] * (bounds[1][-1] - bounds[1][0]) + bounds[1][0]
    current_beam.append(point)

  
  
  candidates = [list(c) for c in current_beam]
  
  

  for iteration in range(0, n_iterations):

      pool = np.array([generate_neighbors(c, step_size = step_size) for c in current_beam]).reshape(-1, 2)

      pool = np.unique(pool, axis=0)
     
      pool = [p for p in pool if in_bounds(p) and list(p) not in candidates]
      if len(pool) == 0:
          break
      
    
      
      
      current_beam = sorted(list(pool), key = lambda key: objective(key))
      
      
      candidates.extend([list(c) for c in current_beam[0:3]])
    

      current_beam = current_beam[0:3]
      
  solution = min(current_beam, key = lambda key: objective(key))
  return [solution, objective(solution), candidates]

# seed the pseudorandom number generator
seed(240)
# define range for input
bounds = asarray([[-5.0, 5.0], [-5.0, 5.0]])
# define the total iterations
n_iterations = 100



# define the maximum step size
step_size = 0.022

# candidates to consider
k = 3
# perform the local beam search

lbs_solution, lbs_solution_value, lbs_candidates = local_beam_search(objective, bounds, step_size, k, n_iterations)

print('Done!')
print('f(%s) = %f' % (lbs_solution, lbs_solution_value))


Done!
f([-0.01423134  0.00776866]) = 0.052846


In [12]:
# Analysis
all_method_candidates = np.array([lbs_candidates])
ack_figure = create_ackley_figure(all_method_candidates)
ack_figure.show()

## Analysis

In the local beam search algorithm, the hyperparameter I chose for the step size is 0.022. A higher step size seems to cause the algorithm to struggle to find the global optimum. The k size seems to not cause a major effect on the algorithm's performance in finding the minimum. As shown in the visual graph, there is a very small region toward the bottom of the plane near the minimum.


## Three Experiment Graph


![](https://drive.google.com/uc?id=1SLpiKSG0sPMiZYMJCLKnR31WRZWJbSvB)


In [13]:
# All Three Experiment Graphs

min_size = len(sa_candidates) if len(shcr_candidates) < len(sa_candidates) else len(shcr_candidates)
min_size = len(lbs_candidates) if len(lbs_candidates) < min_size else min_size

all_method_candidates = np.array([shcr_candidates[0:min_size], sa_candidates[0:min_size], lbs_candidates[0:min_size]])
ack_figure = create_ackley_figure(all_method_candidates)
ack_figure.show()


## Problem 2: CSP
---

Consider the following constraint satisfaction problem. A linear graph has nodes of the following colors:

- Red
- Yellow
- Green
- Blue
- Violet

Each node has a domain of {1, 2, ..., 9}.

Each node type has the following constraints on its value:

- Red - No contraints
- Yellow - equals the rightmost digit of of the product of all its neighbors
- Green - equals the rightmost digit of the sum of all its neighbors 
- Blue - equals the leftmost digit of the sum of all its neighbors
- Violet - equals the leftmost digit of the product of all of its neighbors

As a reminder here is the pseudo code for the Min-Conflicts search algorithm:

![minconflicts](https://images2017.cnblogs.com/blog/1126979/201712/1126979-20171224140802287-1871895433.png)

**Notes:**

- It's possible that you won't converge to a solution in a single run. Try a few runs to see if you get to a solution.
- The testcases are to show you what a problem looks like, we will test/grade your program on different examples.

### Part 1) Implementation
Complete the function ```solve_csp``` defined below. You may find some helper functions useful.

In [14]:
from numpy import meshgrid as meshgrid
from operator import mul
from functools import reduce


def get_right_most_digit(num):
    num_int = str(int(abs(num)))
    return int(num_int[-1])
    
def get_left_most_digit(num):
    num_int = str(int(abs(num)))
    return int(num_int[0])


def constraint_check_given_type(assignment, nodes, arc_dict, isProd=False, digit_func=get_right_most_digit, node='Y'):

    assigns = np.array([assignment[neighbor] for neighbor in arc_dict[node] if assignment[neighbor] != -1])

    digit = None
    if assigns.shape[0] == 0:
        if -1 in assignment.values():
            return True
        return False
    else:
        digit = digit_func(reduce(mul, assigns, 1) if isProd else sum(assigns))


    if int(assignment[node]) == int(digit):
        return True
    return False


def check_constraints(assignment, nodes, arc_dict):
    """ 
        assignment:{Y: 0, B: 1}
        nodes: YGVRB
        arc_dict: {Y: [G, V], ...}


        Constraints:
        Red - No contraints
        Yellow - equals the rightmost digit of of the product of all its neighbors
        Green - equals the rightmost digit of the sum of all its neighbors
        Blue - equals the leftmost digit of the sum of all its neighbors
        Violet - equals the leftmost digit of the product of all of its neighbors

    """

    no_conflict_list = []

    for node in nodes:
        if node == 'R':
            no_conflict_list.append(True)
            continue
        elif node == 'Y':
            result = constraint_check_given_type(assignment, nodes, arc_dict, isProd = True, digit_func=get_right_most_digit, node='Y')
            no_conflict_list.append(result)
        elif node == 'G':
            result = constraint_check_given_type(assignment, nodes, arc_dict, isProd = False, digit_func=get_right_most_digit, node='G')
            no_conflict_list.append(result)
        elif node == 'B':
            result = constraint_check_given_type(assignment, nodes, arc_dict, isProd = False, digit_func=get_left_most_digit, node='B')
            no_conflict_list.append(result)
        elif node == 'V':
            result = constraint_check_given_type(assignment, nodes, arc_dict, isProd = True, digit_func=get_left_most_digit, node='V')
            no_conflict_list.append(result)

    
    return np.all(True == np.array(no_conflict_list)), no_conflict_list



def find_min_conflict_value(node, assignment, nodes, arc_dict):

    conflict_counts = []
    old_assignment_value = assignment[node]
    for i in range(0, 9):
        assignment[node] = i + 1
        isSuccess, no_conflict_list = check_constraints(assignment, nodes, arc_dict)
        conflict_counts.append(no_conflict_list.count(False))
    assignment[node] = old_assignment_value
    

    return conflict_counts.index(min(conflict_counts)) + 1


def solve_csp(nodes, arcs, max_steps):
    """
    This function solves the csp using the MinConflicts Search Algorithm.

    :param nodes, a list of letters that indicates what type of node it is,
                  the index of the node in the list indicates its id
                  letters = {R, Y, G, B, V}
                
    :param arcs,  a list of tuples that contains two numbers, indicating the 
                  IDs of the nodes the arc connects. 
                
    :param max_steps, max number of steps to make before giving up

    returns a list of values for the solution to the CSP where the 
             index of the value corresponds the value for that given node.
    """
    domain = list(range(1, 10))

    arc_dict = dict({})

    for idx1,idx2 in arcs:
        if nodes[idx1] not in arc_dict:
            arc_dict[nodes[idx1]] = []
        if nodes[idx2] not in arc_dict:
            arc_dict[nodes[idx2]] = []
        arc_dict[nodes[idx1]].append(nodes[idx2])
        arc_dict[nodes[idx2]].append(nodes[idx1])
    

    ### YOUR CODE HERE ###

    # we randomly assign a few of the variables first and the rest we apply the min_conflict function.

    current_assignment = dict({node : random.choice(domain) if random.choice([0, 1]) == 1 else -1 for idx, node in enumerate(nodes)})

    
    for nodeChosen in nodes:
        current_assignment[nodeChosen] = find_min_conflict_value(nodeChosen, current_assignment, nodes, arc_dict)



  

    for step in range(0, max_steps):
        isSuccess, check_list = check_constraints(current_assignment, nodes, arc_dict)
        if isSuccess:
            return [current_assignment[n] for n in nodes]

        conflicted_variables = [nodes[idx] for idx, no_conflict in enumerate(check_list) if not(no_conflict)]
        random_variable = random.choice(list(conflicted_variables))
        newAssignment = find_min_conflict_value(random_variable, current_assignment, nodes, arc_dict)
        current_assignment[random_variable] = newAssignment

    return []

### Test Cases

Below we've included 4 test cases to help you debug your code. Your submitted code will be tested on other cases as well, but if your implementation of the above Min-Conflicts search algorithm is able to solve these problems, you should be good to go.

In [15]:
# test Case 1

nodes = 'YGVRB'
arcs = [(0,1), (0,2), (1,2), (1,3), (1,4), (2,3), (2,4)]
max_steps = 1000

for _ in range(max_steps):
    sol = solve_csp(nodes, arcs, max_steps)
    if sol != []:
        print(nodes)
        break
        
all_solutions = [[1, 1, 1, 7, 2],[2, 1, 2, 4, 3],[2, 6, 7, 6, 1],[2, 8, 9, 6, 1],
                 [3, 3, 1, 5, 4],[6, 2, 8, 7, 1],[6, 7, 8, 2, 1],[6, 9, 4, 8, 1]]

if sol == []:
    print('No solution')
else:
    if sol in all_solutions:
        print('Solution found:', sol)
    else:
        print('ERROR: False solution found:', sol)

YGVRB
Solution found: [1, 1, 1, 7, 2]


In [16]:
# test Case 2

nodes = 'YVBGR'
arcs = [(0,1), (0,2), (1,3), (2,4)]
max_steps = 1000

for _ in range(max_steps):
    sol = solve_csp(nodes, arcs, max_steps)
    if sol != []:
        print(nodes)
        break
        
all_solutions = [[1, 1, 1, 1, 9], [1, 3, 7, 3, 6], [1, 7, 3, 7, 2], [1, 9, 9, 9, 8]]

if sol == []:
    print('No solution')
else:
    if sol in all_solutions:
        print('Solution found:', sol)
    else:
        print('ERROR: False solution found:', sol)

YVBGR
Solution found: [1, 1, 1, 1, 9]


In [17]:
# test Case 3

nodes = 'VYGBR'
arcs = [(0,1), (1,2), (2,3), (3,4)]
max_steps = 1000

for _ in range(max_steps):
    sol = solve_csp(nodes, arcs, max_steps)
    if sol != []:
        print(nodes)
        break
        
all_solutions = [[2, 2, 1, 9, 8],[3, 3, 1, 8, 7],[4, 4, 1, 7, 6],[5, 5, 1, 6, 5],[5, 5, 3, 8, 5],
                 [6, 6, 1, 5, 4],[7, 7, 1, 4, 3],[8, 8, 1, 3, 2],[8, 8, 6, 8, 2],[9, 9, 1, 2, 1]]

if sol == []:
    print('No solution')
else:
    if sol in all_solutions:
        print('Solution found:', sol)
    else:
        print('ERROR: False solution found:', sol)

VYGBR
Solution found: [4, 4, 1, 7, 6]


In [18]:
# test Case 4

nodes = 'YGVBR'
arcs = [(0,1), (0,2), (1,3), (2,3), (3,4), (1,2)]
max_steps = 1000

for _ in range(max_steps):
    sol = solve_csp(nodes, arcs, max_steps)
    if sol != []:
        print(nodes)
        break
        
all_solutions = [[4, 4, 1, 9, 4],[4, 7, 2, 1, 1],[4, 7, 2, 1, 2],[4, 7, 2, 1, 3],[4, 7, 2, 1, 4],
                 [4, 7, 2, 1, 5],[4, 7, 2, 1, 6],[4, 7, 2, 1, 7],[4, 7, 2, 1, 8],[4, 7, 2, 1, 9],
                 [4, 8, 3, 1, 1],[4, 8, 3, 1, 2],[4, 8, 3, 1, 3],[4, 8, 3, 1, 4],[4, 8, 3, 1, 5],
                 [4, 8, 3, 1, 6],[4, 8, 3, 1, 7],[4, 8, 3, 1, 8],[5, 1, 5, 1, 4],[5, 1, 5, 1, 5],
                 [5, 1, 5, 1, 6],[5, 1, 5, 1, 7],[5, 1, 5, 1, 8],[5, 1, 5, 1, 9]]

if sol == []:
    print('No solution')
else:
    if sol in all_solutions:
        print('Solution found:', sol)
    else:
        print('ERROR: False solution found:', sol)

YGVBR
Solution found: [5, 1, 5, 1, 4]


## Problem 3: The N-Rooks Problem
---

Rooks can move any number of squares horizontally or vertically on a chess board. The n rooks problem is to arrange rooks on an $n\times n$ board in such a way that none of the rooks could bump into another by making any of its possible horizontal or vertical moves. 

For this problem, the variables are each column (labeled 0, 1, ... , $ n-1$), the the domain consists of each possible row (also labeled 0, 1, ... , $ n-1$). In each column we place a rook on row 0, row 1, ... , row $n-1$.

For example, if $n=2$ we have only two solutions to this problem:

    R @
    @ R 
    
or

    @ R
    R @ 
   

### Part 1)
How many possible solutions are there to this CSP, in terms of n?  Also, give a simple proof that your answer is correct.

The number of possible solutions for this CSP, in terms of n is n!



Proof:

For a given n x n board, let's place the first rook on the board. The number of possible squares we can place the rook on the board is n * n. Now let's place the second rook on the board. The number of possible squares for the second rook is (n - 1) * (n - 1) since the first rook attacks one row and one column, thus decreasing the number of rows by one. If we continue this placement, the total number of solutions is (n * n) * (n-1 * n - 1) * (n-2 * n - 2) ... = n! * n!. We don't care about the ordering we place the rooks in so we divide the product by n!. So the number of possible solutions is (n! * n!) / n! = n!


### Python Library to solve CSPs

One useful Python module for solving these types of problems is called *constraint*. In the next cell you'll see how to load this module into a Jupyter notebook running in Colab. 

We'll use this module to solve the following simple CSP. Suppose our variables are x and y, and the values they are allowed to assume are numbers in the domain {1, 2, ... , 100}, and with constraints be that $x^2=y$ and that $x$ is odd.

In [19]:
# The following line imports the constraint module into a Jupyter notebook running in Colab.
# (This only needs to be done once per session)

!pip install python-constraint

# Let's load all the functions available in this module
# (This only needs to be done once per session)

from constraint import *

# Now we initialize a new problem and add the two variables.
problem = Problem()
problem.addVariables(["x", "y"], list(range(1, 101)))

# So far there are no constraints. If we solve the problem with no constraints, 
# then every possible combination of x and y values from 1 to 100 are valid solutions.
solutions = problem.getSolutions()

# Total number of solutions
print( len(solutions) )

10000


In [20]:
# Add the given constraints:
problem.addConstraint(lambda a, b: a**2 == b and (a % 2) == 1, ("x", "y"))

# There are only 5 solutions that satisfy those constraints:
solutions = problem.getSolutions()
print( len(solutions) )

5


In [21]:
# Here are all 5 solutions:


print(solutions)

[{'x': 9, 'y': 81}, {'x': 7, 'y': 49}, {'x': 5, 'y': 25}, {'x': 3, 'y': 9}, {'x': 1, 'y': 1}]


Notice that the solutions consist of a list of dictionaries, where each dictionary represents a solution. For example, the first solution is {'x': 9, 'y': 81}, since with $x=9$ and $y=81$ it's true that $x^2=y$.

### Part 2) The n-rooks problem revisited

Modify the example before to solve the n-rooks problem.

In [22]:
### YOUR CODE HERE ###

rook_count = 8


domain = list(range(0, rook_count))
variables = [str(i) for i in domain]

n_rooks_problem = Problem()
n_rooks_problem.addVariables(variables, domain)


counter = 1
for i in range(0, rook_count):
    for j in range(counter, rook_count):
        n_rooks_problem.addConstraint(lambda v1, v2: v1 != v2, (str(i), str(j)))
    counter += 1

solutions = n_rooks_problem.getSolutions()


### Part 3)

*   How many ways are there of arranging $8$ rooks on an $8\times8$ board so that none impede the others?
*   How many ways are there arranging $11$ rooks on an $11\times11$ board so that none impede the others?


1. There are 8! or 40,320 ways to arrange 8 rooks on a 8 x 8 board so none impede the others
2. There are 11! or 39916800 ways to arrange 11 rooks on a 11 x 11 board so that none impede the others.



